## Начало крайней лабораторной в этом семестре, эх...

#### Что необходимо сделать:
Развернуть и запустить проект по реализации обучения с подкреплением для игры "Крестики-нолики". Перевести проект на библиотеку gymnasium и современную версию Python. Реализовать агента для игры "Крестики-нолики" в виде отдельного класса (по примеру из лекции). Переписать основной цикл обучения для работы с отдельным классом агента (по примеру из лекции). Выполнить тестирование новой версии программы.

Наши крестики-нолики: https://github.com/nczempin/gym-tic-tac-toe

#### Перевод проекта на библиотеку gymnasium
Gymnasium — это открытая библиотека Python, которая предоставляет стандартизированные среды для разработки и тестирования алгоритмов обучения с подкреплением (Reinforcement Learning, RL). Ранее была известна как OpenAI Gym (до 2022 года), но теперь развивается под новым именем.

Библиотека позволяет разработчикам RL-агентов взаимодействовать с различными симуляциями — от простых игровых задач до сложных физических моделей. Gymnasium упрощает процесс тестирования и сравнения алгоритмов благодаря унифицированному интерфейсу.

**Основные возможности Gymnasium:**
1. Унифицированный API для RL-сред:

- Gymnasium предлагает стандартный интерфейс для взаимодействия с RL-средами, включающий методы reset(), step(action), и другие.
- Это позволяет легко переключаться между различными средами без изменения кода агента.
2. Разнообразие встроенных сред:

- Библиотека включает множество готовых симуляций, от простых (например, CartPole, MountainCar) до сложных (например, робототехника, Atari-игры).
- Среды подразделяются на категории: контроль, игры, физика, робототехника и др.
3. Поддержка классических задач RL:

- Среды для изучения классических задач, таких как балансировка маятника, решение головоломок, управление роботами и т.д.
4. Гибкость создания пользовательских сред:

- Gymnasium позволяет разработчикам создавать собственные симуляции, соответствующие API.
5. Совместимость с различными RL-библиотеками:

- Gymnasium интегрируется с популярными RL-фреймворками, такими как Stable-Baselines3, Ray RLlib, TensorFlow Agents, PyTorch RL и другими.
6. Визуализация:

- Среды могут визуализироваться, что упрощает отладку и демонстрацию работы алгоритмов.

**Основные функции Gymnasium:**
- Инициализация среды (gymnasium.make()): позволяет создавать экземпляр среды по её имени.
- Сброс среды (reset()): возвращает начальное состояние среды и другую информацию.
- Выполнение действия (step(action)): передаёт действие агенту и возвращает результат.
- Закрытие среды (close()): очищает ресурсы, связанные со средой.
- Режим рендеринга (render()): позволяет визуализировать работу среды.

In [2]:
import gymnasium as gym
from gymnasium import spaces

class TicTacToeEnv(gym.Env):
    metadata = {'render.modes': ['human']}
    
    symbols = ['O', ' ', 'X']

    def __init__(self):
        super().__init__()
        self.action_space = spaces.Discrete(9) # Дискретное пространство действий (0–8), соответствующее номерам клеток на игровом поле (от 0 до 8).
        self.observation_space = spaces.Discrete(9 * 3 * 2) # Дискретное пространство состояний. Расчёт: 9 клеток × 3 состояния (пустая, крестик, нолик) × 2 игрока (на чей ход).
        self.reset()

    def step(self, action):
        done = False
        reward = 0

        p, square = action  # p - игрок (1 или -1), square - номер клетки

        board = self.state['board']
        proposed = board[square] 
        om = self.state['on_move'] 
        if proposed != 0:  # Клетка уже занята
            print(f"Незаконный ход: Квадрат {square} уже занят.")
            done = True
            reward = -1 * om 
        if p != om:  # Не тот игрок на ходу
            print(f"Незаконный ход: игрок {p} не находится в движении")
            done = True
            reward = -1 * om
        else:
            board[square] = p
            self.state['on_move'] = -p

        for i in range(3):
            # Горизонтали и вертикали
            if (board[i * 3] == p and board[i * 3 + 1] == p and board[i * 3 + 2] == p) or \
               (board[i] == p and board[i + 3] == p and board[i + 6] == p):
                reward = p
                done = True
                break

        # Диагонали
        if (board[0] == p and board[4] == p and board[8] == p) or \
           (board[2] == p and board[4] == p and board[6] == p):
            reward = p
            done = True
                
        return self.state, reward, done, {}

    def reset(self):
        self.state = {}
        self.state['board'] = [0, 0, 0, 0, 0, 0, 0, 0, 0] 
        self.state['on_move'] = 1 
        return self.state, {}

    def render(self, close=False):
        if close:
            return
        print("on move: " , self.symbols[self.state['on_move']+1])
        for i in range (9):
            print (self.symbols[self.state['board'][i]+1], end=" ")
            if ((i % 3) == 2):
                print()

    def move_generator(self):
        moves = []
        for i in range(9):
            if self.state['board'][i] == 0:
                p = self.state['on_move']
                m = [p, i]
                moves.append(m)
        return moves

#### Реализация агента
В контексте обучения с подкреплением (Reinforcement Learning, RL) агент — это программный компонент, который взаимодействует с окружающей средой (environment) с целью научиться выбирать оптимальные действия для достижения своей цели.

**Основные аспекты агента:**
1. Что делает агент?

- Агент принимает решения: в каждом состоянии среды он выбирает действие (например, на какую клетку походить в крестиках-ноликах или как двигаться в игре).
- Он учится выбирать действия, которые максимизируют его "награду" (reward), получаемую от среды.
2. Как агент учится?

- Агент улучшает свою стратегию на основе опыта взаимодействия со средой.
- Этот процесс осуществляется с использованием алгоритмов обучения с подкреплением (например, Q-learning, глубокое Q-обучение или методы политики).

Ключевые элементы агента:
1. Наблюдение (Observation): Агент воспринимает текущее состояние среды. Это может быть, например, игровое поле, показания датчиков или изображение. Наблюдение агент получает в виде данных от среды.
2. Действие (Action): В каждом шаге агент выбирает действие из допустимого набора действий. Этот набор зависит от правил среды (например, куда можно походить в игре).
3. Политика (Policy): Политика — это стратегия, которой следует агент, чтобы выбирать действия.
Она может быть:
- Детерминированной: одно и то же состояние всегда приводит к одному и тому же действию.
- Стохастической: для одного состояния агент выбирает действие с определённой вероятностью.
4. Награда (Reward): После выполнения действия агент получает награду — числовое значение, отражающее, насколько его действие было "хорошим".
Награды помогают агенту оценивать свои действия и формировать полезное поведение.
5. Функция ценности (Value Function):
Это внутренняя оценка агента, которая отражает, насколько "хорошим" или "перспективным" является определённое состояние.
Она позволяет агенту предсказывать долгосрочные последствия своих действий.
6. Алгоритм обучения:
Агент использует алгоритмы для обновления своей политики и функции ценности, основываясь на полученных наградах.
Примеры: метод Q-learning, методы на основе градиента политики (Policy Gradient), алгоритмы Actor-Critic и т. д.


In [3]:
import random

class Agent:
    def __init__(self, symbol):
        self.symbol = symbol  # Символ игрока (1 - X, -1 - O)
    
    def get_action(self, moves):
        return random.choice(moves)  # Выбираем случайный ход из доступных

#### Основной цикл обучения

In [4]:
# Основной цикл обучения (работа с отдельным классом агента)

# Создание среды для игры в крестики-нолики
environment = TicTacToeEnv()

# Создание агента (играющего крестиками)
agent = Agent(symbol=1)

num_episodes = 100  # Количество эпизодов (игр) для обучения
collected_rewards = [] # Список для хранения наград/побед в каждом эпизоде 

# Переменная для отслеживания символа и текущего игрока
oom = 1

for i in range(num_episodes):
    # Сброс среды и начало нового эпизода
    state, _ = environment.reset() 

    # Общая награда за эпизод
    total_reward = 0

    # Флаг завершения игры
    done = False
    om = oom 

    # Максимум 9 ходов, поскольку поле 3x3 
    for j in range(9): 
        moves = environment.move_generator() 

        # Ходов нет, заканчиваем игру
        if not moves:
            break

        
        if len(moves) == 1:
            move = moves[0]    # Если остался один ход на основе стратегии
        else:
            move = agent.get_action(moves)   # Агент выбирает ход на основе стратегии

        # Выполнение хода и обновление состояния игры
        next_state, reward, done, info = environment.step(move)
        total_reward += reward
        state = next_state

        # Отображаем текущее состояние игры
        environment.render()

        if done:
            break

        om = -om    # Смена игрока

    collected_rewards.append(total_reward)

    print(f"Episode {i+1}, Total Reward: {total_reward}")
    average_reward = sum(collected_rewards) / len(collected_rewards)
    print(f"Average Reward: {average_reward}")

on move:  O
    X 
      
      
on move:  X
  O X 
      
      
on move:  O
  O X 
    X 
      
on move:  X
O O X 
    X 
      
on move:  O
O O X 
  X X 
      
on move:  X
O O X 
  X X 
    O 
on move:  O
O O X 
  X X 
X   O 
Episode 1, Total Reward: 1
Average Reward: 1.0
on move:  O
X     
      
      
on move:  X
X     
      
O     
on move:  O
X X   
      
O     
on move:  X
X X   
      
O O   
on move:  O
X X   
  X   
O O   
on move:  X
X X O 
  X   
O O   
on move:  O
X X O 
  X X 
O O   
on move:  X
X X O 
O X X 
O O   
on move:  O
X X O 
O X X 
O O X 
Episode 2, Total Reward: 1
Average Reward: 1.0
on move:  O
  X   
      
      
on move:  X
  X   
      
    O 
on move:  O
  X   
      
  X O 
on move:  X
  X   
      
O X O 
on move:  O
X X   
      
O X O 
on move:  X
X X   
  O   
O X O 
on move:  O
X X   
  O X 
O X O 
on move:  X
X X   
O O X 
O X O 
on move:  O
X X X 
O O X 
O X O 
Episode 3, Total Reward: 1
Average Reward: 1.0
on move:  O
      
  X   
      
o